In [30]:
import os
import numpy as np
import pandas as pd

import tempfile

from rdkit import Chem
from rdkit.Chem import AllChem
import deepchem as dc

from deepchem.utils import download_url, load_from_disk

from sklearn.ensemble import RandomForestRegressor
from deepchem.utils.rdkit_utils import load_complex
from deepchem.utils.geometry_utils import compute_pairwise_distances

from deepchem.utils.evaluate import Evaluator
import pandas as pd

In [2]:
data_dir = dc.utils.get_data_dir()
dataset_file = os.path.join(data_dir, "pdbbind_core_df.csv.gz")

if not os.path.exists(dataset_file):
    print('File does not exist. Downloading file...')
    download_url("https://s3-us-west-1.amazonaws.com/deepchem.io/datasets/pdbbind_core_df.csv.gz")
    print('File downloaded...')

raw_dataset = load_from_disk(dataset_file)
raw_dataset = raw_dataset[['pdb_id', 'smiles', 'label']]

In [3]:
from openmm.app import PDBFile
from pdbfixer import PDBFixer

#from deepchem.utils.vina_utils import prepare_inputs
from deepchem.utils.docking_utils import prepare_inputs
from tqdm.auto import tqdm
import itertools
import os
import sys
sys.path.append(os.getcwd() + '/..')
from pyDowker.DowkerComplex import DowkerComplex
from pyDowker.TwoParameterUtils import grid_ECP
from DowkerFeaturizer import DowkerFeaturizer, DowkerBifiFeaturizer
from pyrivet import rivet
import xgboost as xgb

In [4]:
# consider one protein-ligand complex for visualization
pdbid = raw_dataset['pdb_id'].iloc[0]
ligand = raw_dataset['smiles'].iloc[0]

In [5]:
%%time
fixer = PDBFixer(pdbid=pdbid)
PDBFile.writeFile(fixer.topology, fixer.positions, open('%s.pdb' % (pdbid), 'w'))

p, m = None, None
# fix protein, optimize ligand geometry, and sanitize molecules
try:
    p, m = prepare_inputs('%s.pdb' % (pdbid), ligand)
except:
    print('%s failed PDB fixing' % (pdbid)) 

if p and m:  # protein and molecule are readable by RDKit
    print(pdbid, p.GetNumAtoms())
    Chem.rdmolfiles.MolToPDBFile(p, '%s.pdb' % (pdbid))
    Chem.rdmolfiles.MolToPDBFile(m, 'ligand_%s.pdb' % (pdbid))

2d3u 8689
CPU times: user 12.7 s, sys: 138 ms, total: 12.9 s
Wall time: 13.4 s


[10:56:15] WARNING: not removing hydrogen atom without neighbors
[10:56:19] UFFTYPER: Unrecognized atom type: S_5+4 (7)


In [6]:
pdbids = raw_dataset['pdb_id'].values
ligand_smiles = raw_dataset['smiles'].values

In [7]:
%%time
for (pdbid, ligand) in zip(pdbids, ligand_smiles):
    fixer = PDBFixer(url='https://files.rcsb.org/download/%s.pdb' % (pdbid))
    PDBFile.writeFile(fixer.topology, fixer.positions, open('%s.pdb' % (pdbid), 'w'))
  
    p, m = None, None
    # skip pdb fixing for speed
    try:
        p, m = prepare_inputs('%s.pdb' % (pdbid), ligand, replace_nonstandard_residues=False,
                          remove_heterogens=False, remove_water=False,
                          add_hydrogens=False)
    except:
        print('%s failed sanitization' % (pdbid)) 

    if p and m:  # protein and molecule are readable by RDKit
        Chem.rdmolfiles.MolToPDBFile(p, '%s.pdb' % (pdbid))
        Chem.rdmolfiles.MolToPDBFile(m, 'ligand_%s.pdb' % (pdbid))

[10:56:44] UFFTYPER: Unrecognized atom type: S_5+4 (7)
[10:56:53] UFFTYPER: Warning: hybridization set to SP3 for atom 17
[10:56:54] UFFTYPER: Warning: hybridization set to SP3 for atom 6
[10:56:55] UFFTYPER: Warning: hybridization set to SP3 for atom 1
[10:56:55] UFFTYPER: Unrecognized atom type: S_5+4 (21)
[10:57:04] UFFTYPER: Warning: hybridization set to SP3 for atom 20
[10:57:09] UFFTYPER: Warning: hybridization set to SP3 for atom 19
[10:57:11] UFFTYPER: Warning: hybridization set to SP3 for atom 29
[10:57:25] UFFTYPER: Unrecognized atom type: S_5+4 (39)
[10:57:44] UFFTYPER: Warning: hybridization set to SP3 for atom 33
[10:57:57] UFFTYPER: Unrecognized atom type: S_5+4 (11)
[10:57:58] UFFTYPER: Unrecognized atom type: S_5+4 (47)
[10:58:03] UFFTYPER: Unrecognized atom type: S_5+4 (1)
[10:58:10] UFFTYPER: Warning: hybridization set to SP3 for atom 6
[10:58:13] UFFTYPER: Unrecognized atom type: S_5+4 (47)
[10:58:19] UFFTYPER: Unrecognized atom type: S_5+4 (28)
[10:58:25] UFFTYPER: 

1hfs failed sanitization


[11:00:52] UFFTYPER: Warning: hybridization set to SP3 for atom 20
[11:01:01] Explicit valence for atom # 1800 C, 5, is greater than permitted
[11:01:01] UFFTYPER: Unrecognized atom type: S_5+4 (11)
[11:01:02] UFFTYPER: Warning: hybridization set to SP3 for atom 11
[11:01:10] UFFTYPER: Warning: hybridization set to SP3 for atom 9
[11:01:10] UFFTYPER: Warning: hybridization set to SP3 for atom 23
[11:01:11] UFFTYPER: Warning: hybridization set to SP3 for atom 8
[11:01:11] UFFTYPER: Warning: hybridization set to SP3 for atom 12
[11:01:11] UFFTYPER: Warning: hybridization set to SP3 for atom 34
[11:01:11] UFFTYPER: Warning: hybridization set to SP3 for atom 41


CPU times: user 1min 51s, sys: 921 ms, total: 1min 52s
Wall time: 4min 29s


In [8]:
proteins = [f for f in os.listdir('.') if len(f) == 8 and f.endswith('.pdb')]
ligands = [f for f in os.listdir('.') if f.startswith('ligand') and f.endswith('.pdb')]

In [9]:
# Handle failed sanitizations
failures = set([f[:-4] for f in proteins]) - set([f[7:-4] for f in ligands])
for pdbid in failures:
    proteins.remove(pdbid + '.pdb')

In [10]:
len(proteins), len(ligands)

(190, 190)

In [11]:
pdbids = [f[:-4] for f in proteins]
small_dataset = raw_dataset[raw_dataset['pdb_id'].isin(pdbids)]
labels = small_dataset.label

In [12]:
proteins = [pdbid+'.pdb' for pdbid in pdbids]
ligands = ['ligand_'+pdbid+'.pdb' for pdbid in pdbids]
labels = [small_dataset.label[small_dataset['pdb_id'][small_dataset['pdb_id']==pdbid].index.to_list()[0]] for pdbid in pdbids]

In [13]:
list(zip(ligands,proteins))

[('ligand_1sln.pdb', '1sln.pdb'),
 ('ligand_2v7a.pdb', '2v7a.pdb'),
 ('ligand_2x0y.pdb', '2x0y.pdb'),
 ('ligand_2d1o.pdb', '2d1o.pdb'),
 ('ligand_2yge.pdb', '2yge.pdb'),
 ('ligand_3k5v.pdb', '3k5v.pdb'),
 ('ligand_2x00.pdb', '2x00.pdb'),
 ('ligand_3g2z.pdb', '3g2z.pdb'),
 ('ligand_3b68.pdb', '3b68.pdb'),
 ('ligand_3uo4.pdb', '3uo4.pdb'),
 ('ligand_2jdm.pdb', '2jdm.pdb'),
 ('ligand_4dew.pdb', '4dew.pdb'),
 ('ligand_2vl4.pdb', '2vl4.pdb'),
 ('ligand_2qft.pdb', '2qft.pdb'),
 ('ligand_2xb8.pdb', '2xb8.pdb'),
 ('ligand_3kgp.pdb', '3kgp.pdb'),
 ('ligand_3pe2.pdb', '3pe2.pdb'),
 ('ligand_4tmn.pdb', '4tmn.pdb'),
 ('ligand_2xbv.pdb', '2xbv.pdb'),
 ('ligand_3bpc.pdb', '3bpc.pdb'),
 ('ligand_1f8b.pdb', '1f8b.pdb'),
 ('ligand_3ao4.pdb', '3ao4.pdb'),
 ('ligand_4gid.pdb', '4gid.pdb'),
 ('ligand_3dxg.pdb', '3dxg.pdb'),
 ('ligand_1w3l.pdb', '1w3l.pdb'),
 ('ligand_1mq6.pdb', '1mq6.pdb'),
 ('ligand_3su2.pdb', '3su2.pdb'),
 ('ligand_3g0w.pdb', '3g0w.pdb'),
 ('ligand_3su5.pdb', '3su5.pdb'),
 ('ligand_1w3k

In [14]:
fp_featurizer = dc.feat.ContactCircularFingerprint(size=2048)

In [15]:
features = fp_featurizer.featurize(zip(ligands, proteins))


[11:06:45] Explicit valence for atom # 2207 C, 5, is greater than permitted
Mol CC[C@@H]1C2OC2(=O)[C@@H]2C(O)N2C(=O)[C@H]1NC(=O)[C@H](CO)NC(=O)[C@H](CO)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CCC(N)=O)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCSC)NC(=O)[C@@H](NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](C)NC(=O)[C@H](CCC(N)=O)NC(=O)[C@H](CC1=CNC=N1)NC(=O)[C@@H](NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](C)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CO)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CCCNC(=N)N)NC(=O)[C@H](CC(=O)O)NC(=O)[C@H](CO)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CC(N)=O)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CCC(N)=O)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CS)NC(=O)[C@H](C)NC(=O)[C@H](CCCNC(=N)N)NC(=O)[C@H](CCSC)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H](NC(=O)[C@H](CCCCN)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CS)NC(=O)CNC(=O)[C@H](CCC(=O)O)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CCCNC(=N)N)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CCSC)NC(=O)[C@H](CCCNC(=N)N)NC(=O)[C@H](CC

In [16]:
train_scores = []
test_scores = []

for seed in range(0,100):
    #seed = 42 # Set a random seed to get stable results

    dataset = dc.data.NumpyDataset(X=features, y=labels, ids=pdbids)
    train_dataset, test_dataset = dc.splits.RandomSplitter().train_test_split(dataset, seed=seed)
    sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
    sklearn_model.random_state = seed
    model = dc.models.SklearnModel(sklearn_model)
    model.fit(train_dataset)

    metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

    evaluator = Evaluator(model, train_dataset, [])
    train_r2score = evaluator.compute_model_performance([metric])
    #print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))
    train_scores.append(train_r2score['pearson_r2_score'])
    
    
    evaluator = Evaluator(model, test_dataset, [])
    test_r2score = evaluator.compute_model_performance([metric])
    #print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))
    test_scores.append(test_r2score['pearson_r2_score'])

In [17]:
print("avg RF Train R^2:", np.mean(train_scores),"\pm",np.std(train_scores))
print("avg RF Test R^2:", np.mean(test_scores),"\pm",np.std(test_scores))

avg RF Train R^2: 0.4124904368866754 \pm 0.0253180284313709
avg RF Test R^2: 0.0205629388048493 \pm 0.02616211959046954


In [25]:


dgm0 = []
dgm1 = []

for datapoint in tqdm(zip(ligands,proteins)):
    fragments = load_complex(datapoint, add_hydrogens=False)
    for (frag1, frag2) in itertools.combinations(fragments, 2):
        ligand_atoms = np.array([a.GetSymbol() for a in frag1[1].GetAtoms()])
        protein_atoms = np.array([a.GetSymbol() for a in frag2[1].GetAtoms()])
        dist = compute_pairwise_distances(frag1[0],frag2[0])
        local_dgm0 = []
        local_dgm1 = []
        for la in ['C', 'N', 'O', 'S', 'P', 'F', 'Cl', 'Br', 'I']:
            for pa in ['C', 'N', 'O', 'S']:
                local_dist = dist[ligand_atoms==la,:][:,protein_atoms==pa]
                if local_dist.size>0:
                    dowker = DowkerComplex(local_dist,max_filtration=4.5)
                    st = dowker.create_simplex_tree(max_dimension=2,m=1, filtration="Sublevel")
                    st.compute_persistence()
                    local_dgm0.append(st.persistence_intervals_in_dimension(0))
                    local_dgm1.append(st.persistence_intervals_in_dimension(1))
                else:
                    local_dgm0.append(np.empty((0,2)))
                    local_dgm1.append(np.empty((0,2)))
        dgm0.append(local_dgm0)
        dgm1.append(local_dgm1)

0it [00:00, ?it/s]

[11:24:57] Explicit valence for atom # 2197 C, 5, is greater than permitted
Mol CC[C@H](C)[C@H](NC(=O)CNC(=O)[C@@H]1CCCN1C(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CO)NC(=O)[C@H](CCSC)NC(=O)CNC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H](NC(=O)[C@H](C)NC(=O)[C@@H](NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](NC(=O)CNC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](C)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@@H](NC(=O)[C@H](CC(=O)O)NC(=O)[C@H](CO)NC(=O)[C@H](CCCCN)NC(=O)[C@@H](NC(=O)[C@H](CO)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCCCN)NC(=O)[C@H](CC(N)=O)NC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@H](C)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CO)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@@H]1CCCN1C(=O)[C@H](C)NC(=O)[C@@H](NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CCCCN)NC(=O)[C@@H](NC(=O)[C@@H]1CCCN1C(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCCCN)NC(=O)[C@H](C)NC(=O)CNC(=O)[C@H](C)NC(=O)[C@H](CC1=CNC=N1)NC(=O)[C@H](C)NC(=O)[C@@H](N=C(O)[C@H](CC1CCC(O[PH](O)(O)O)CC1)NC(=O)[

In [27]:
from gudhi.representations import BettiCurve,Landscape
bc = Landscape(num_landscapes = 4, resolution=1024, sample_range = (0,100))
#bc = BettiCurve(predefined_grid=np.linspace(0,100,2048))

bc0 = np.array([np.concatenate(bc.fit_transform(d)) for d in dgm0])
bc1 = np.array([np.concatenate(bc.fit_transform(d)) for d in dgm1])
vectors = bc1#np.concatenate([bc0,bc1],axis=1)

/home/niklas/anaconda3/envs/Graphs/lib/python3.9/site-packages/gudhi/representations/vector_methods.py:200: RuntimeWarning: invalid value encountered in subtract
  tent_functions = np.maximum(heights[None, :] - np.abs(x_values[:, None] - midpoints[None, :]), 0)


In [28]:
vectors

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [31]:
train_scores = []
test_scores = []

for seed in tqdm(range(0,100)):
    #seed = 42 # Set a random seed to get stable results

    dataset = dc.data.NumpyDataset(X=vectors, y=labels, ids=pdbids)
    train_dataset, test_dataset = dc.splits.RandomSplitter().train_test_split(dataset, seed=seed)
    #sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
    sklearn_model = xgb.XGBRegressor()
    sklearn_model.random_state = seed
    model = dc.models.SklearnModel(sklearn_model)
    model.fit(train_dataset)

    metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

    evaluator = Evaluator(model, train_dataset, [])
    train_r2score = evaluator.compute_model_performance([metric])
    #print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))
    train_scores.append(train_r2score['pearson_r2_score'])
    
    
    evaluator = Evaluator(model, test_dataset, [])
    test_r2score = evaluator.compute_model_performance([metric])
    #print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))
    test_scores.append(test_r2score['pearson_r2_score'])

  0%|          | 0/100 [00:00<?, ?it/s]

In [32]:
print("avg RF Train R^2:", np.mean(train_scores),"\pm",np.std(train_scores))
print("avg RF Test R^2:", np.mean(test_scores),"\pm",np.std(test_scores))

avg RF Train R^2: 0.30618433427639435 \pm 0.023839738515719775
avg RF Test R^2: 0.02796138718893609 \pm 0.03449490050904955


In [35]:

mn_featurizer = DowkerFeaturizer(m=8,size=1024)
features = mn_featurizer.featurize(zip(ligands, proteins))

train_scores = []
test_scores = []

for seed in range(0,100):
    #seed = 42 # Set a random seed to get stable results

    dataset = dc.data.NumpyDataset(X=features, y=labels, ids=pdbids)
    train_dataset, test_dataset = dc.splits.RandomSplitter().train_test_split(dataset, seed=seed)
    #sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
    sklearn_model = xgb.XGBRegressor()
    sklearn_model.random_state = seed
    model = dc.models.SklearnModel(sklearn_model)
    model.fit(train_dataset)

    metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

    evaluator = Evaluator(model, train_dataset, [])
    train_r2score = evaluator.compute_model_performance([metric])
    #print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))
    train_scores.append(train_r2score['pearson_r2_score'])
    
    
    evaluator = Evaluator(model, test_dataset, [])
    test_r2score = evaluator.compute_model_performance([metric])
    #print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))
    test_scores.append(test_r2score['pearson_r2_score'])
    
print("avg RF Train R^2:", np.mean(train_scores),"\pm",np.std(train_scores))
print("avg RF Test R^2:", np.mean(test_scores),"\pm",np.std(test_scores))

[12:06:25] Explicit valence for atom # 2197 C, 5, is greater than permitted
Mol CC[C@H](C)[C@H](NC(=O)CNC(=O)[C@@H]1CCCN1C(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CO)NC(=O)[C@H](CCSC)NC(=O)CNC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H](NC(=O)[C@H](C)NC(=O)[C@@H](NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](NC(=O)CNC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](C)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@@H](NC(=O)[C@H](CC(=O)O)NC(=O)[C@H](CO)NC(=O)[C@H](CCCCN)NC(=O)[C@@H](NC(=O)[C@H](CO)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCCCN)NC(=O)[C@H](CC(N)=O)NC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@H](C)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CO)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@@H]1CCCN1C(=O)[C@H](C)NC(=O)[C@@H](NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CCCCN)NC(=O)[C@@H](NC(=O)[C@@H]1CCCN1C(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCCCN)NC(=O)[C@H](C)NC(=O)CNC(=O)[C@H](C)NC(=O)[C@H](CC1=CNC=N1)NC(=O)[C@H](C)NC(=O)[C@@H](N=C(O)[C@H](CC1CCC(O[PH](O)(O)O)CC1)NC(=O)[

avg RF Train R^2: 0.9977866745599796 \pm 0.0014953448683773245
avg RF Test R^2: 0.017239910041839664 \pm 0.020393609627580255


In [36]:
datapoint = list(zip(ligands,proteins))[0]
bifi_featurizer = DowkerBifiFeaturizer(m_max=8,size=128)
my_features = bifi_featurizer._featurize(datapoint)

In [37]:

bifi_featurizer = DowkerBifiFeaturizer(m_max=8,size=256)
bifi_features = bifi_featurizer.featurize(zip(ligands, proteins))

train_scores = []
test_scores = []

for seed in tqdm(range(0,100)):
    #seed = 42 # Set a random seed to get stable results

    dataset = dc.data.NumpyDataset(X=bifi_features, y=labels, ids=pdbids)
    train_dataset, test_dataset = dc.splits.RandomSplitter().train_test_split(dataset, seed=seed)
    sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
    sklearn_model.random_state = seed
    model = dc.models.SklearnModel(sklearn_model)
    model.fit(train_dataset)

    metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

    evaluator = Evaluator(model, train_dataset, [])
    train_r2score = evaluator.compute_model_performance([metric])
    #print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))
    train_scores.append(train_r2score['pearson_r2_score'])
    
    
    evaluator = Evaluator(model, test_dataset, [])
    test_r2score = evaluator.compute_model_performance([metric])
    #print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))
    test_scores.append(test_r2score['pearson_r2_score'])
    
print("avg RF Train R^2:", np.mean(train_scores),"\pm",np.std(train_scores))
print("avg RF Test R^2:", np.mean(test_scores),"\pm",np.std(test_scores))

[12:19:37] Explicit valence for atom # 2199 C, 5, is greater than permitted
Mol CC[C@H](C)[C@H](NC(=O)CNC(=O)[C@@H]1CCCN1C(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H]1CCCN1C(=O)[C@H](CO)NC(=O)[C@H](CCSC)NC(=O)CNC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@@H](NC(=O)[C@H](C)NC(=O)[C@@H](NC(=O)[C@H](CCC(=O)O)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](NC(=O)CNC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](C)NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@@H](NC(=O)[C@H](CC(=O)O)NC(=O)[C@H](CO)NC(=O)[C@H](CCCCN)NC(=O)[C@@H](NC(=O)[C@H](CO)NC(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCCCN)NC(=O)[C@H](CC(N)=O)NC(=O)[C@H](CC1=CC=C(O)C=C1)NC(=O)[C@H](C)NC(=O)[C@H](CC(C)C)NC(=O)[C@H](CO)NC(=O)[C@H](CCC(=O)O)NC(=O)[C@@H]1CCCN1C(=O)[C@H](C)NC(=O)[C@@H](NC(=O)[C@H](CC1=CNC2=C1C=CC=C2)NC(=O)[C@H](CCCCN)NC(=O)[C@@H](NC(=O)[C@@H]1CCCN1C(=O)[C@H](CC1=CC=CC=C1)NC(=O)[C@H](CCCCN)NC(=O)[C@H](C)NC(=O)CNC(=O)[C@H](C)NC(=O)[C@H](CC1=CNC=N1)NC(=O)[C@H](C)NC(=O)[C@@H](N=C(O)[C@H](CC1CCC(O[PH](O)(O)O)CC1)NC(=O)[

  0%|          | 0/100 [00:00<?, ?it/s]

avg RF Train R^2: 0.9257179179233863 \pm 0.005954865670456129
avg RF Test R^2: 0.06465461527627611 \pm 0.055500111631671824


In [38]:
print("avg RF Train R^2:", np.mean(train_scores),"\pm",np.std(train_scores))
print("avg RF Test R^2:", np.mean(test_scores),"\pm",np.std(test_scores))

avg RF Train R^2: 0.9257179179233863 \pm 0.005954865670456129
avg RF Test R^2: 0.06465461527627611 \pm 0.055500111631671824


In [39]:
counter = 0
for datapoint in list(zip(ligands,proteins)):
    if not (bifi_featurizer._featurize(datapoint)==mn_featurizer._featurize(datapoint)).all():
        counter+=1
        
print(counter)

ValueError: operands could not be broadcast together with shapes (147456,) (73728,) 

In [25]:
from DowkerFeaturizer import DowkerECPFeaturizer

ecp_featurizer = DowkerECPFeaturizer(m_max=8,size=128)
ecp_features = ecp_featurizer.featurize(zip(ligands, proteins))

train_scores = []
test_scores = []

for seed in tqdm(range(0,100)):
    #seed = 42 # Set a random seed to get stable results

    dataset = dc.data.NumpyDataset(X=ecp_features, y=labels, ids=pdbids)
    train_dataset, test_dataset = dc.splits.RandomSplitter().train_test_split(dataset, seed=seed)
    sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
    sklearn_model.random_state = seed
    model = dc.models.SklearnModel(sklearn_model)
    model.fit(train_dataset)

    metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

    evaluator = Evaluator(model, train_dataset, [])
    train_r2score = evaluator.compute_model_performance([metric])
    #print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))
    train_scores.append(train_r2score['pearson_r2_score'])
    
    
    evaluator = Evaluator(model, test_dataset, [])
    test_r2score = evaluator.compute_model_performance([metric])
    #print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))
    test_scores.append(test_r2score['pearson_r2_score'])
    
print("avg RF Train R^2:", np.mean(train_scores),"\pm",np.std(train_scores))
print("avg RF Test R^2:", np.mean(test_scores),"\pm",np.std(test_scores))

[15:15:24] Explicit valence for atom # 1849 O, 3, is greater than permitted
Mol CC[C@H](C)[C@H](N)C(=O)N[C@H](C(=O)NCC(=O)NCC(=O)N[C@@H](CCC(N)=O)C(=O)N[C@@H](CCC(=O)O)C(=O)N[C@H]1CSSC[C@@H](C(=O)N2CCC[C@H]2C(=O)N[C@@H](CC2=CNC3=C2C=CC=C3)C(=O)N[C@@H](CCC(N)=O)C(=O)N[C@@H](C)C(=O)N[C@@H](CC(C)C)C(=O)N[C@@H](CC(C)C)C(=O)N[C@H](C(=O)N[C@@H](CC(N)=O)C(=O)N[C@@H](CCC(=O)O)C(=O)N[C@@H](CCC(=O)O)C(=O)N[C@@H](CC(N)=O)C(=O)N[C@@H](CCC(=O)O)C(=O)NCC(=O)N[C@@H](CC2=CC=CC=C2)C(=O)N[C@H]2CSSC[C@@H](C(=O)N[C@@H](CC(C)C)C(=O)N[C@@H](CC3=CC=C(O)C=C3)C(=O)N[C@@H](CCC(N)=O)C(=O)N[C@@H](C)C(=O)N[C@@H](CCCCN)C(=O)N[C@@H](CCCNC(=N)N)C(=O)N[C@@H](CC3=CC=CC=C3)C(=O)N[C@@H](CCCCN)C(=O)N[C@H](C(=O)N[C@@H](CCCNC(=N)N)C(=O)N[C@H](C(=O)NCC(=O)N[C@@H](CC(=O)O)C(=O)N[C@@H](CCCNC(=N)N)C(=O)N[C@@H](CC(N)=O)C(=O)N[C@H](C(=O)N[C@@H](CCC(=O)O)C(=O)N[C@@H](CCC(N)=O)C(=O)N[C@@H](CCC(=O)O)C(=O)N[C@@H](CCC(=O)O)C(=O)NCC(=O)NCC(=O)N[C@@H](CCC(=O)O)C(=O)N[C@@H](C)C(=O)N[C@H](C(=O)N[C@@H](CC3=CNC=N3)C(=O)N[C@@H](CCC(=O)O)C(=O

Failed to featurize datapoint 17. Appending empty array.
Failed to featurize datapoint 18. Appending empty array.
Failed to featurize datapoint 19. Appending empty array.
Failed to featurize datapoint 20. Appending empty array.
[15:15:49] Explicit valence for atom # 9 C, 5, is greater than permitted
Mol [H]O[C@@]1([H])[C@]([H])(O[H])[C@]([H])(O[H])N2[C@]([H])(C([H])([H])OC2([H])([H])N([H])C([H])([H])C([H])([H])C([H])([H])C([H])([H])C([H])([H])C([H])([H])C([H])([H])C([H])([H])[H])[C@]1([H])O[H] failed sanitization
Failed to featurize datapoint 21. Appending empty array.
Failed to featurize datapoint 22. Appending empty array.
Failed to featurize datapoint 23. Appending empty array.
Failed to featurize datapoint 24. Appending empty array.
Failed to featurize datapoint 25. Appending empty array.
Failed to featurize datapoint 26. Appending empty array.
Failed to featurize datapoint 27. Appending empty array.
Failed to featurize datapoint 28. Appending empty array.
Failed to featurize datap

Failed to featurize datapoint 94. Appending empty array.
Failed to featurize datapoint 95. Appending empty array.
Failed to featurize datapoint 96. Appending empty array.
Failed to featurize datapoint 97. Appending empty array.
Failed to featurize datapoint 98. Appending empty array.
[15:16:26] Explicit valence for atom # 11 C, 5, is greater than permitted
Mol [H]O[C@]1([H])C([H])([H])C([H])([H])N2[C@@]1([H])[C@]([H])(C(F)(F)F)OC2([H])([H])N([H])[C@@]1([H])C([H])([H])C([H])([H])[C@]([H])(C([H])([H])N([H])[H])[C@]([H])(Cl)[C@@]1([H])C([H])([H])[H] failed sanitization
Failed to featurize datapoint 99. Appending empty array.
[15:16:26] Explicit valence for atom # 29 C, 5, is greater than permitted
Mol [H]O[C@]([H])(N([H])[C@@]1([H])[C@@]([H])([C@]([H])(O[H])N([H])[C@@]2([H])N([H])C([H])([H])[C@]([H])(Cl)C([H])([H])C2([H])[H])C([H])([H])[C@@]([H])(Cl)C([H])([H])[C@@]1([H])OC([H])([H])[H])[C@]1([H])SC([H])([H])[C@@]([H])(C([H])([H])N(C([H])([H])[H])C2([H])([H])OC([H])([H])C([H])([H])N2[H])[

  0%|          | 0/100 [00:00<?, ?it/s]

NameError: name 'bifi_features' is not defined

# Refined Dataset

In [40]:
# Uncomment to featurize all of PDBBind's "refined" set
mn_featurizer = DowkerFeaturizer(m=1,size=1024)
pdbbind_tasks, (train_dataset, valid_dataset, test_dataset), transformers = dc.molnet.load_pdbbind(
     featurizer=mn_featurizer, set_name="refined", reload=True,
     data_dir='pdbbind_data', save_dir='pdbbind_data')

[12:48:30] Explicit valence for atom # 61 O, 3, is greater than permitted
Mol O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O=C[C@@H]1CCCN1.[H]NCC(=O)N([H])[C@@H](CO[H])C(=O)N([H])[C@H](C(=O)N([H])[C@@H](C)C(=O)N([H])CC(=O)N([H])[C@H](C=O)CC1=CC=CC=C1)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C(=O)N([H])[C@]1(CCC(=O)O)OC1=O)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C=O)CO[H].[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])CC(=O)N1CCC[C@H]1C(=O)N([H])[C@@H](CCC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)N([H])CC=O.[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC(=O)N([H])[H].[H]N[C@@H](CC(C)C)C(=O)N([H])[C@H](C(=O)N([H])[C@H](C(=O)N([H])[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC1=CC=C(O[H])C=C1)[C@@H](C)CC)[C@@H](C)O[H].[H]N[C@@H](CC1=CC=C(O[H])C=C1)C(=O)N([H])[C@H](C=O)[C@@H](C)O[H].[H]N[C@@H](CCCN([H])C(N([H])[H])=[N+]([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)[N+]1([H])O2C(=O)[C@@]21CO[H].[H]N[C@H](C(=O)N([H])[C@@H](CC

In [41]:
from sklearn.ensemble import RandomForestRegressor

from deepchem.utils.evaluate import Evaluator
import pandas as pd
seed = 42 # Set a random seed to get stable results
sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
#sklearn_model = xgb.XGBRegressor()
sklearn_model.random_state = seed
model = dc.models.SklearnModel(sklearn_model)
model.fit(train_dataset)
# use Pearson correlation so metrics are > 0
metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

evaluator = Evaluator(model, train_dataset, [])
train_r2score = evaluator.compute_model_performance([metric])
print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))

evaluator = Evaluator(model, test_dataset, [])
test_r2score = evaluator.compute_model_performance([metric])
print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))

RF Train set R^2 0.955810
RF Test set R^2 0.476820


In [42]:
# Uncomment to featurize all of PDBBind's "refined" set
bifi_featurizer = DowkerBifiFeaturizer(m_max=8,size=1024)
pdbbind_tasks, (train_dataset, valid_dataset, test_dataset), transformers = dc.molnet.load_pdbbind(
     featurizer=bifi_featurizer, set_name="refined", reload=True,
     data_dir='pdbbind_data', save_dir='pdbbind_data')

[13:08:28] Explicit valence for atom # 61 O, 3, is greater than permitted
Mol O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O=C[C@@H]1CCCN1.[H]NCC(=O)N([H])[C@@H](CO[H])C(=O)N([H])[C@H](C(=O)N([H])[C@@H](C)C(=O)N([H])CC(=O)N([H])[C@H](C=O)CC1=CC=CC=C1)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C(=O)N([H])[C@]1(CCC(=O)O)OC1=O)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C=O)CO[H].[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])CC(=O)N1CCC[C@H]1C(=O)N([H])[C@@H](CCC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)N([H])CC=O.[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC(=O)N([H])[H].[H]N[C@@H](CC(C)C)C(=O)N([H])[C@H](C(=O)N([H])[C@H](C(=O)N([H])[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC1=CC=C(O[H])C=C1)[C@@H](C)CC)[C@@H](C)O[H].[H]N[C@@H](CC1=CC=C(O[H])C=C1)C(=O)N([H])[C@H](C=O)[C@@H](C)O[H].[H]N[C@@H](CCCN([H])C(N([H])[H])=[N+]([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)[N+]1([H])O2C(=O)[C@@]21CO[H].[H]N[C@H](C(=O)N([H])[C@@H](CC

In [43]:
seed = 42 # Set a random seed to get stable results
sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt')
#sklearn_model = xgb.XGBRegressor()
sklearn_model.random_state = seed
model = dc.models.SklearnModel(sklearn_model)
model.fit(train_dataset)
# use Pearson correlation so metrics are > 0
metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

evaluator = Evaluator(model, train_dataset, [])
train_r2score = evaluator.compute_model_performance([metric])
print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))

evaluator = Evaluator(model, test_dataset, [])
test_r2score = evaluator.compute_model_performance([metric])
print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))

RF Train set R^2 0.955891
RF Test set R^2 0.513524


In [44]:
train_R2 = []
test_R2 = []
#oob = []


for j in tqdm(range(1,13)):
    # Uncomment to featurize all of PDBBind's "refined" set
    size = 1024
    bifi_featurizer = DowkerBifiFeaturizer(m_max=j,size=size)
    pdbbind_tasks, (train_dataset, valid_dataset, test_dataset), transformers = dc.molnet.load_pdbbind(
         featurizer=bifi_featurizer, set_name="refined", reload=True,
         data_dir='pdbbind_data', save_dir='pdbbind_data')
    seed = 42 # Set a random seed to get stable results
    sklearn_model = RandomForestRegressor(n_estimators=100, max_features='sqrt', oob_score=True)
    #sklearn_model = xgb.XGBRegressor()
    sklearn_model.random_state = seed
    model = dc.models.SklearnModel(sklearn_model)
    model.fit(train_dataset)
    # use Pearson correlation so metrics are > 0
    metric = dc.metrics.Metric(dc.metrics.pearson_r2_score)

    evaluator = Evaluator(model, train_dataset, [])
    train_r2score = evaluator.compute_model_performance([metric])
    print("RF Train set R^2 %f" % (train_r2score["pearson_r2_score"]))

    evaluator = Evaluator(model, test_dataset, [])
    test_r2score = evaluator.compute_model_performance([metric])
    print("RF Test set R^2 %f" % (test_r2score["pearson_r2_score"]))

    train_R2.append(train_r2score["pearson_r2_score"])
    test_R2.append(test_r2score["pearson_r2_score"])
    #oob.append(sklearn_model.oob_score_)
    with open("xgb_bifi_results_size={}.txt".format(size), 'w') as file:
        # Writing data to a file
        df = pd.DataFrame(columns=['m', 'train R^2', 'test R^2', 'oob']) 
        df['m'] = range(1,j+1)
        df['train R^2'] = train_R2
        df['test R^2'] = test_R2
        #df['oob'] = oob
        file.write(df.to_latex(index=False))

  0%|          | 0/12 [00:00<?, ?it/s]

[13:54:06] Explicit valence for atom # 61 O, 3, is greater than permitted
Mol O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O=C[C@@H]1CCCN1.[H]NCC(=O)N([H])[C@@H](CO[H])C(=O)N([H])[C@H](C(=O)N([H])[C@@H](C)C(=O)N([H])CC(=O)N([H])[C@H](C=O)CC1=CC=CC=C1)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C(=O)N([H])[C@]1(CCC(=O)O)OC1=O)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C=O)CO[H].[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])CC(=O)N1CCC[C@H]1C(=O)N([H])[C@@H](CCC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)N([H])CC=O.[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC(=O)N([H])[H].[H]N[C@@H](CC(C)C)C(=O)N([H])[C@H](C(=O)N([H])[C@H](C(=O)N([H])[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC1=CC=C(O[H])C=C1)[C@@H](C)CC)[C@@H](C)O[H].[H]N[C@@H](CC1=CC=C(O[H])C=C1)C(=O)N([H])[C@H](C=O)[C@@H](C)O[H].[H]N[C@@H](CCCN([H])C(N([H])[H])=[N+]([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)[N+]1([H])O2C(=O)[C@@]21CO[H].[H]N[C@H](C(=O)N([H])[C@@H](CC

RF Train set R^2 0.957177
RF Test set R^2 0.497869


[14:11:56] Explicit valence for atom # 61 O, 3, is greater than permitted
Mol O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O=C[C@@H]1CCCN1.[H]NCC(=O)N([H])[C@@H](CO[H])C(=O)N([H])[C@H](C(=O)N([H])[C@@H](C)C(=O)N([H])CC(=O)N([H])[C@H](C=O)CC1=CC=CC=C1)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C(=O)N([H])[C@]1(CCC(=O)O)OC1=O)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C=O)CO[H].[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])CC(=O)N1CCC[C@H]1C(=O)N([H])[C@@H](CCC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)N([H])CC=O.[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC(=O)N([H])[H].[H]N[C@@H](CC(C)C)C(=O)N([H])[C@H](C(=O)N([H])[C@H](C(=O)N([H])[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC1=CC=C(O[H])C=C1)[C@@H](C)CC)[C@@H](C)O[H].[H]N[C@@H](CC1=CC=C(O[H])C=C1)C(=O)N([H])[C@H](C=O)[C@@H](C)O[H].[H]N[C@@H](CCCN([H])C(N([H])[H])=[N+]([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)[N+]1([H])O2C(=O)[C@@]21CO[H].[H]N[C@H](C(=O)N([H])[C@@H](CC

RF Train set R^2 0.955416
RF Test set R^2 0.459163


[14:32:37] Explicit valence for atom # 61 O, 3, is greater than permitted
Mol O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O=C[C@@H]1CCCN1.[H]NCC(=O)N([H])[C@@H](CO[H])C(=O)N([H])[C@H](C(=O)N([H])[C@@H](C)C(=O)N([H])CC(=O)N([H])[C@H](C=O)CC1=CC=CC=C1)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C(=O)N([H])[C@]1(CCC(=O)O)OC1=O)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C=O)CO[H].[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])CC(=O)N1CCC[C@H]1C(=O)N([H])[C@@H](CCC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)N([H])CC=O.[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC(=O)N([H])[H].[H]N[C@@H](CC(C)C)C(=O)N([H])[C@H](C(=O)N([H])[C@H](C(=O)N([H])[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC1=CC=C(O[H])C=C1)[C@@H](C)CC)[C@@H](C)O[H].[H]N[C@@H](CC1=CC=C(O[H])C=C1)C(=O)N([H])[C@H](C=O)[C@@H](C)O[H].[H]N[C@@H](CCCN([H])C(N([H])[H])=[N+]([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)[N+]1([H])O2C(=O)[C@@]21CO[H].[H]N[C@H](C(=O)N([H])[C@@H](CC

RF Train set R^2 0.954718
RF Test set R^2 0.445279


[14:56:15] Explicit valence for atom # 61 O, 3, is greater than permitted
Mol O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O.O=C[C@@H]1CCCN1.[H]NCC(=O)N([H])[C@@H](CO[H])C(=O)N([H])[C@H](C(=O)N([H])[C@@H](C)C(=O)N([H])CC(=O)N([H])[C@H](C=O)CC1=CC=CC=C1)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C(=O)N([H])[C@]1(CCC(=O)O)OC1=O)[C@@H](C)O[H].[H]NCC(=O)N([H])[C@H](C=O)CO[H].[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])CC(=O)N1CCC[C@H]1C(=O)N([H])[C@@H](CCC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)N([H])CC=O.[H]N[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC(=O)N([H])[H].[H]N[C@@H](CC(C)C)C(=O)N([H])[C@H](C(=O)N([H])[C@H](C(=O)N([H])[C@@H](CC(=O)N([H])[H])C(=O)N([H])[C@@H](CC1=CN([H])C2=C1C=CC=C2)C(=O)N([H])[C@H](C=O)CC1=CC=C(O[H])C=C1)[C@@H](C)CC)[C@@H](C)O[H].[H]N[C@@H](CC1=CC=C(O[H])C=C1)C(=O)N([H])[C@H](C=O)[C@@H](C)O[H].[H]N[C@@H](CCCN([H])C(N([H])[H])=[N+]([H])[H])C(=O)N([H])[C@@H](CC1=CC=CC=C1)C(=O)[N+]1([H])O2C(=O)[C@@]21CO[H].[H]N[C@H](C(=O)N([H])[C@@H](CC

In [ ]:
with open("rf_bifi_results_size={}.txt".format(size), 'w') as file:
    # Writing data to a file
    df = pd.DataFrame(columns=['m', 'train R^2', 'test R^2']) 
    df['m'] = range(1,13)
    df['train R^2'] = train_R2
    df['test R^2'] = test_R2

    file.write(df.to_latex(index=False))

In [1]:
df

NameError: name 'df' is not defined